In [650]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
pd.set_option('display.max_columns', None)

## Background
West Nile virus is most commonly spread to humans through infected mosquitos. Around 20% of people who become infected with the virus develop symptoms ranging from a persistent fever, to serious neurological illnesses that can result in death.

In 2002, the first human cases of West Nile virus were reported in Chicago. By 2004 the City of Chicago and the Chicago Department of Public Health (CDPH) had established a comprehensive surveillance and control program that is still in effect today.

Every week from late spring through the fall, mosquitos in traps across the city are tested for the virus. The results of these tests influence when and where the city will spray airborne pesticides to control adult mosquito populations.

----
## Problem Statement

Given weather, location, testing, and spraying data, build a machine learning model that can predict when and where different species of mosquitos will test positive for West Nile virus. A more accurate method of predicting outbreaks of West Nile virus in mosquitos will help the City of Chicago and CPHD more efficiently and effectively allocate resources towards preventing transmission of this potentially deadly virus. 

In [651]:
train = pd.read_csv('../assets/train.csv')
test = pd.read_csv('../assets/test.csv')
weather = pd.read_csv('../assets/weather.csv')
spray = pd.read_csv('../assets/spray.csv')

In [652]:
weather.head(10)

Station        Date  Tmax  Tmin Tavg Depart  DewPoint WetBulb Heat Cool  \
0        1  2007-05-01    83    50   67     14        51      56    0    2   
1        2  2007-05-01    84    52   68      M        51      57    0    3   
2        1  2007-05-02    59    42   51     -3        42      47   14    0   
3        2  2007-05-02    60    43   52      M        42      47   13    0   
4        1  2007-05-03    66    46   56      2        40      48    9    0   
5        2  2007-05-03    67    48   58      M        40      50    7    0   
6        1  2007-05-04    66    49   58      4        41      50    7    0   
7        2  2007-05-04    78    51    M      M        42      50    M    M   
8        1  2007-05-05    66    53   60      5        38      49    5    0   
9        2  2007-05-05    66    54   60      M        39      50    5    0   

  Sunrise Sunset CodeSum Depth Water1 SnowFall PrecipTotal StnPressure  \
0    0448   1849             0      M      0.0        0.00       29.10   
1       -      -             M      M        M        0.00       29.18   
2    0447   1850      BR     0      M      0.0        0.00       29.38   
3       -      -   BR HZ     M      M        M        0.00       29.44   
4    0446   1851             0      M      0.0        0.00       29.39   
5       -      -      HZ     M      M        M        0.00       29.46   
6    0444   1852      RA     0      M      0.0           T       29.31   
7       -      -             M      M        M        0.00       29.36   
8    0443   1853             0      M      0.0           T       29.40   
9       -      -             M      M        M           T       29.46   

  SeaLevel  ResultSpeed  ResultDir AvgSpeed  
0    29.82          1.7         27      9.2  
1    29.82          2.7         25      9.6  
2    30.09         13.0          4     13.4  
3    30.08         13.3          2     13.4  
4    30.12         11.7          7     11.9  
5    30.12         12.9          6     13.2  
6    30.05         10.4          8     10.8  
7    30.04         10.1          7     10.4  
8    30.10         11.7          7     12.0  
9    30.09         11.2          7     11.5

In [653]:
weather.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2944 entries, 0 to 2943
Data columns (total 22 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   Station      2944 non-null   int64  
 1   Date         2944 non-null   object 
 2   Tmax         2944 non-null   int64  
 3   Tmin         2944 non-null   int64  
 4   Tavg         2944 non-null   object 
 5   Depart       2944 non-null   object 
 6   DewPoint     2944 non-null   int64  
 7   WetBulb      2944 non-null   object 
 8   Heat         2944 non-null   object 
 9   Cool         2944 non-null   object 
 10  Sunrise      2944 non-null   object 
 11  Sunset       2944 non-null   object 
 12  CodeSum      2944 non-null   object 
 13  Depth        2944 non-null   object 
 14  Water1       2944 non-null   object 
 15  SnowFall     2944 non-null   object 
 16  PrecipTotal  2944 non-null   object 
 17  StnPressure  2944 non-null   object 
 18  SeaLevel     2944 non-null   object 
 19  Result

In [654]:
weather['Date'] = pd.to_datetime(weather['Date'])

In [655]:
weather.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2944 entries, 0 to 2943
Data columns (total 22 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   Station      2944 non-null   int64         
 1   Date         2944 non-null   datetime64[ns]
 2   Tmax         2944 non-null   int64         
 3   Tmin         2944 non-null   int64         
 4   Tavg         2944 non-null   object        
 5   Depart       2944 non-null   object        
 6   DewPoint     2944 non-null   int64         
 7   WetBulb      2944 non-null   object        
 8   Heat         2944 non-null   object        
 9   Cool         2944 non-null   object        
 10  Sunrise      2944 non-null   object        
 11  Sunset       2944 non-null   object        
 12  CodeSum      2944 non-null   object        
 13  Depth        2944 non-null   object        
 14  Water1       2944 non-null   object        
 15  SnowFall     2944 non-null   object        
 16  Precip

In [656]:
weather.isnull().sum()

Station        0
Date           0
Tmax           0
Tmin           0
Tavg           0
Depart         0
DewPoint       0
WetBulb        0
Heat           0
Cool           0
Sunrise        0
Sunset         0
CodeSum        0
Depth          0
Water1         0
SnowFall       0
PrecipTotal    0
StnPressure    0
SeaLevel       0
ResultSpeed    0
ResultDir      0
AvgSpeed       0
dtype: int64

Although there are no null values, according to the data dictionary, T = Trace amounts and M = Missing data.

In [657]:
weather['SnowFall'].unique()

array(['0.0', 'M', '  T', '0.1'], dtype=object)

In [658]:
weather['PrecipTotal'].unique()

array(['0.00', '  T', '0.13', '0.02', '0.38', '0.60', '0.14', '0.07',
       '0.11', '0.09', '1.01', '0.28', '0.04', '0.08', '0.01', '0.53',
       '0.19', '0.21', '0.32', '0.39', '0.31', '0.42', '0.27', '0.16',
       '0.58', '0.93', '0.05', '0.34', '0.15', '0.35', 'M', '0.40',
       '0.66', '0.30', '0.24', '0.43', '1.55', '0.92', '0.89', '0.17',
       '0.03', '1.43', '0.97', '0.26', '1.31', '0.06', '0.46', '0.29',
       '0.23', '0.41', '0.45', '0.83', '1.33', '0.91', '0.48', '0.37',
       '0.88', '2.35', '1.96', '0.20', '0.25', '0.18', '0.67', '0.36',
       '0.33', '1.28', '0.74', '0.76', '0.71', '0.95', '1.46', '0.12',
       '0.52', '0.64', '0.22', '1.24', '0.72', '0.73', '0.65', '1.61',
       '1.22', '0.50', '1.05', '2.43', '0.59', '2.90', '2.68', '1.23',
       '0.62', '6.64', '3.07', '1.44', '1.75', '0.82', '0.80', '0.86',
       '0.63', '0.55', '1.03', '0.70', '1.73', '1.38', '0.44', '1.14',
       '1.07', '3.97', '0.87', '0.78', '1.12', '0.68', '0.10', '0.61',
       '0.

Interestingly, T was always inputted with 2 spaces in front. '  T'

In [659]:
weather.columns

Index(['Station', 'Date', 'Tmax', 'Tmin', 'Tavg', 'Depart', 'DewPoint',
       'WetBulb', 'Heat', 'Cool', 'Sunrise', 'Sunset', 'CodeSum', 'Depth',
       'Water1', 'SnowFall', 'PrecipTotal', 'StnPressure', 'SeaLevel',
       'ResultSpeed', 'ResultDir', 'AvgSpeed'],
      dtype='object')

## Impute Values
----
### Impute Trace Values
As trace values just mean very small amounts, impute all trace values as 0.01

In [660]:
trace = weather.isin(['  T']).sum()

trace_df = []
for key, value in trace.sort_values(ascending=False).items():
    if value != 0:
        trace_row = []
        trace_row.append(key)
        trace_row.append(value)
        percentage = round(value/weather.shape[0]*100,2)
        trace_row.append(percentage)
        trace_df.append(trace_row)
trace_df = pd.DataFrame(trace_df, columns = ['Feature', 'No. of trace values', 'Percentage of trace values'] )
trace_df

Feature  No. of trace values  Percentage of trace values
0  PrecipTotal                  318                       10.80
1     SnowFall                   12                        0.41

In [661]:
weather.loc[weather['PrecipTotal'] == '  T', ['PrecipTotal']] = 0.01
weather.loc[weather['SnowFall'] == '  T', ['SnowFall']] = 0.01

In [662]:
#Check to make sure all '  T' values are changed
trace = weather.isin(['  T']).sum()
trace

Station        0
Date           0
Tmax           0
Tmin           0
Tavg           0
Depart         0
DewPoint       0
WetBulb        0
Heat           0
Cool           0
Sunrise        0
Sunset         0
CodeSum        0
Depth          0
Water1         0
SnowFall       0
PrecipTotal    0
StnPressure    0
SeaLevel       0
ResultSpeed    0
ResultDir      0
AvgSpeed       0
dtype: int64

----
### Impute Missing Values

In [663]:
missing = weather.isin(['M']).sum()

missing_df = []
for key, value in missing.sort_values(ascending=False).items():
    if value != 0:
        missing_row = []
        missing_row.append(key)
        missing_row.append(value)
        percentage = round(value/weather.shape[0]*100,2)
        missing_row.append(percentage)
        missing_df.append(missing_row)
missing_df = pd.DataFrame(missing_df, columns = ['Feature', 'No. of missing values', 'Percentage of missing values'] )
missing_df

Feature  No. of missing values  Percentage of missing values
0        Water1                   2944                        100.00
1        Depart                   1472                         50.00
2      SnowFall                   1472                         50.00
3         Depth                   1472                         50.00
4          Tavg                     11                          0.37
5          Heat                     11                          0.37
6          Cool                     11                          0.37
7      SeaLevel                      9                          0.31
8       WetBulb                      4                          0.14
9   StnPressure                      4                          0.14
10     AvgSpeed                      3                          0.10
11  PrecipTotal                      2                          0.07

**Observations:** 
- All values in Water1 column are missing. Drop Water1 column.
- Exactly half of the values in these columns are missing: Depart, Depth and SnowFall

In [664]:
weather.drop(columns = 'Water1', inplace = True)

**Impute for PrecipTotal column**
- Assume Stations 1 and 2 have the same PrecipTotal on the same day

In [665]:
weather.loc[weather['PrecipTotal'] == 'M']

Station       Date  Tmax  Tmin Tavg Depart  DewPoint WetBulb Heat Cool  \
117        2 2007-06-28    73    61   67      M        56      61    0    2   
119        2 2007-06-29    71    56   64      M        56      60    1    0   

    Sunrise Sunset CodeSum Depth SnowFall PrecipTotal StnPressure SeaLevel  \
117       -      -             M        M           M       29.43    30.07   
119       -      -             M        M           M       29.47    30.11   

     ResultSpeed  ResultDir AvgSpeed  
117         12.2          2     13.3  
119          7.4          2      8.2

In [666]:
#Find out what were the PrecipTotal values for Station 1 for both of these dates and impute values
weather.loc[117:120]

Station       Date  Tmax  Tmin Tavg Depart  DewPoint WetBulb Heat Cool  \
117        2 2007-06-28    73    61   67      M        56      61    0    2   
118        1 2007-06-29    70    56   63     -8        55      59    2    0   
119        2 2007-06-29    71    56   64      M        56      60    1    0   
120        1 2007-06-30    79    54   67     -5        46      56    0    2   

    Sunrise Sunset CodeSum Depth SnowFall PrecipTotal StnPressure SeaLevel  \
117       -      -             M        M           M       29.43    30.07   
118    0419   1931             0      0.0        0.00       29.41    30.13   
119       -      -             M        M           M       29.47    30.11   
120    0419   1931             0      0.0        0.00       29.41    30.13   

     ResultSpeed  ResultDir AvgSpeed  
117         12.2          2     13.3  
118          7.6          2      8.3  
119          7.4          2      8.2  
120          4.9          3      5.8

In [667]:
#Impute PrecipTotal = 0
weather.loc[weather['PrecipTotal'] == 'M',['PrecipTotal']] = 0

In [668]:
#Check if missing values are still there
weather.loc[weather['PrecipTotal'] == 'M']

Empty DataFrame
Columns: [Station, Date, Tmax, Tmin, Tavg, Depart, DewPoint, WetBulb, Heat, Cool, Sunrise, Sunset, CodeSum, Depth, SnowFall, PrecipTotal, StnPressure, SeaLevel, ResultSpeed, ResultDir, AvgSpeed]
Index: []

In [669]:
#Convert column to float
weather['PrecipTotal'] = weather['PrecipTotal'].apply(float)

**Impute for AvgSpeed**
- Assume Stations 1 and 2 have the same AvgSpeed on the same day

In [670]:
weather.loc[weather['AvgSpeed'] == 'M']

Station       Date  Tmax  Tmin Tavg Depart  DewPoint WetBulb Heat Cool  \
87          2 2007-06-13    86    68   77      M        53      62    0   12   
1745        2 2011-09-14    60    48   54      M        45      51   11    0   
2067        2 2012-08-22    84    72    M      M        51      61    M    M   

     Sunrise Sunset      CodeSum Depth SnowFall  PrecipTotal StnPressure  \
87         -      -                  M        M         0.00           M   
1745       -      -  RA BR HZ FU     M        M         0.01       29.47   
2067       -      -                  M        M         0.00       29.39   

     SeaLevel  ResultSpeed  ResultDir AvgSpeed  
87          M          7.0          5        M  
1745        M          6.0         32        M  
2067        M          4.7         19        M

In [671]:
#Find out what were the AvgSpeed values for Station 1 for these dates and impute values
weather.loc[87,['AvgSpeed']] = weather.loc[86,['AvgSpeed']]
weather.loc[1745,['AvgSpeed']] = weather.loc[1744,['AvgSpeed']]
weather.loc[2067,['AvgSpeed']] = weather.loc[2066,['AvgSpeed']]

In [672]:
#Check if missing values are still there
weather.loc[weather['AvgSpeed'] == 'M']

Empty DataFrame
Columns: [Station, Date, Tmax, Tmin, Tavg, Depart, DewPoint, WetBulb, Heat, Cool, Sunrise, Sunset, CodeSum, Depth, SnowFall, PrecipTotal, StnPressure, SeaLevel, ResultSpeed, ResultDir, AvgSpeed]
Index: []

In [673]:
#Convert column to float
weather['AvgSpeed'] = weather['AvgSpeed'].apply(float)

**Impute for StnPressure**
- Assume Stations 1 and 2 have the same StnPressure on the same day

In [674]:
weather.loc[weather['StnPressure'] == 'M']

Station       Date  Tmax  Tmin Tavg Depart  DewPoint WetBulb Heat Cool  \
87          2 2007-06-13    86    68   77      M        53      62    0   12   
848         1 2009-06-26    86    69   78      7        60       M    0   13   
2410        1 2013-08-10    81    64   73      0        57       M    0    8   
2411        2 2013-08-10    81    68   75      M        55      63    0   10   

     Sunrise Sunset CodeSum Depth SnowFall  PrecipTotal StnPressure SeaLevel  \
87         -      -             M        M          0.0           M        M   
848     0418   1931             0      0.0          0.0           M    29.85   
2410    0454   1900             0      0.0          0.0           M    30.08   
2411       -      -             M        M          0.0           M    30.07   

      ResultSpeed  ResultDir  AvgSpeed  
87            7.0          5       8.6  
848           6.4          4       8.2  
2410          5.3          5       6.5  
2411          6.0          6       7.4

In [675]:
#Find out what were the StnPressure values for Station 1 for these dates and impute values
weather.loc[87,['StnPressure']] = weather.loc[86,['StnPressure']]

#Find out what were the StnPressure values for Station 2 for these dates and impute values
weather.loc[848,['StnPressure']] = weather.loc[849,['StnPressure']]

In [676]:
#As no StnPressure value was measured on 2013-08-10 at both stations, impute the average between the day before and after
avg_stnpressure = weather.loc[[2408,2409,2412,2413],['Station','Date','StnPressure']]
#StnPressure has datatype object because of 'M' and 'T' values
avg_stnpressure['StnPressure'] = avg_stnpressure['StnPressure'].apply(float)
avg_stnpressure = avg_stnpressure['StnPressure'].mean()
avg_stnpressure

29.3475

In [677]:
#Impute StnPressure for 2013-08-10
weather.loc[2410,['StnPressure']] = avg_stnpressure
weather.loc[2411,['StnPressure']] = avg_stnpressure

In [678]:
#Check if missing values are still there
weather.loc[weather['StnPressure'] == 'M']

Empty DataFrame
Columns: [Station, Date, Tmax, Tmin, Tavg, Depart, DewPoint, WetBulb, Heat, Cool, Sunrise, Sunset, CodeSum, Depth, SnowFall, PrecipTotal, StnPressure, SeaLevel, ResultSpeed, ResultDir, AvgSpeed]
Index: []

In [679]:
#Convert column to float
weather['StnPressure'] = weather['StnPressure'].apply(float)

**Impute for WetBulb**
- Assume Stations 1 and 2 have the same WetBulb on the same day

In [680]:
weather.loc[weather['WetBulb'] == 'M']

Station       Date  Tmax  Tmin Tavg Depart  DewPoint WetBulb Heat Cool  \
848         1 2009-06-26    86    69   78      7        60       M    0   13   
2410        1 2013-08-10    81    64   73      0        57       M    0    8   
2412        1 2013-08-11    81    60   71     -2        61       M    0    6   
2415        2 2013-08-12    85    69   77      M        63       M    0   12   

     Sunrise Sunset CodeSum Depth SnowFall  PrecipTotal  StnPressure SeaLevel  \
848     0418   1931             0      0.0         0.00      29.2000    29.85   
2410    0454   1900             0      0.0         0.00      29.3475    30.08   
2412    0455   1859      RA     0      0.0         0.01      29.3500    30.07   
2415       -      -      RA     M        M         0.66      29.2700    29.92   

      ResultSpeed  ResultDir  AvgSpeed  
848           6.4          4       8.2  
2410          5.3          5       6.5  
2412          2.0         27       3.0  
2415          4.5         26       7.7

In [681]:
#Find out what were the WetBulb values for Station 1 for these dates and impute values
weather.loc[2415,['WetBulb']] = weather.loc[2414,['WetBulb']]

#Find out what were the WetBulb values for Station 2 for these dates and impute values
weather.loc[848,['WetBulb']] = weather.loc[849,['WetBulb']]
weather.loc[2410,['WetBulb']] = weather.loc[2411,['WetBulb']]
weather.loc[2412,['WetBulb']] = weather.loc[2413,['WetBulb']]

In [682]:
#Check if missing values are still there
weather.loc[weather['WetBulb'] == 'M']

Empty DataFrame
Columns: [Station, Date, Tmax, Tmin, Tavg, Depart, DewPoint, WetBulb, Heat, Cool, Sunrise, Sunset, CodeSum, Depth, SnowFall, PrecipTotal, StnPressure, SeaLevel, ResultSpeed, ResultDir, AvgSpeed]
Index: []

In [683]:
#Convert column to float
weather['WetBulb'] = weather['WetBulb'].apply(float)

**Impute for SeaLevel**
- Assume Stations 1 and 2 have the same SeaLevel on the same day

In [684]:
weather.loc[weather['SeaLevel'] == 'M']

Station       Date  Tmax  Tmin Tavg Depart  DewPoint  WetBulb Heat Cool  \
87          2 2007-06-13    86    68   77      M        53     62.0    0   12   
832         1 2009-06-18    80    61   71      1        63     67.0    0    6   
994         1 2009-09-07    77    59   68      1        59     62.0    0    3   
1732        1 2011-09-08    75    57   66      0        53     59.0    0    1   
1745        2 2011-09-14    60    48   54      M        45     51.0   11    0   
1756        1 2011-09-20    74    49   62      0        54     58.0    3    0   
2067        2 2012-08-22    84    72    M      M        51     61.0    M    M   
2090        1 2012-09-03    88    71   80     12        70     73.0    0   15   
2743        2 2014-07-23    76    64   70      M        56     61.0    0    5   

     Sunrise Sunset       CodeSum Depth SnowFall  PrecipTotal  StnPressure  \
87         -      -                   M        M         0.00        29.36   
832     0416   1929         RA BR     0      0.0         0.12        29.08   
994     0523   1817            BR     0      0.0         0.00        29.39   
1732    0524   1815            RA     0      0.0         0.01        29.34   
1745       -      -   RA BR HZ FU     M        M         0.01        29.47   
1756    0537   1753  MIFG BCFG BR     0      0.0         0.00        29.26   
2067       -      -                   M        M         0.00        29.39   
2090    0519   1824            BR     0      0.0         0.00        29.17   
2743       -      -                   M        M         0.00        29.47   

     SeaLevel  ResultSpeed  ResultDir  AvgSpeed  
87          M          7.0          5       8.6  
832         M          6.7         16       7.9  
994         M          5.8          3       4.0  
1732        M         13.0          2      13.4  
1745        M          6.0         32       7.3  
1756        M          7.3         18       7.3  
2067        M          4.7         19       5.8  
2090        M          4.6          6       4.4  
2743        M         16.4          2      16.7

In [685]:
#Find out what were the SeaLevel values for Station 1 for these dates and impute values
weather.loc[87,['SeaLevel']] = weather.loc[86,['SeaLevel']]
weather.loc[1745,['SeaLevel']] = weather.loc[1744,['SeaLevel']]
weather.loc[2067,['SeaLevel']] = weather.loc[2066,['SeaLevel']]
weather.loc[2743,['SeaLevel']] = weather.loc[2742,['SeaLevel']]

#Find out what were the SeaLevel values for Station 2 for these dates and impute values
weather.loc[832,['SeaLevel']] = weather.loc[833,['SeaLevel']]
weather.loc[994,['SeaLevel']] = weather.loc[995,['SeaLevel']]
weather.loc[1732,['SeaLevel']] = weather.loc[1733,['SeaLevel']]
weather.loc[1756,['SeaLevel']] = weather.loc[1757,['SeaLevel']]
weather.loc[2090,['SeaLevel']] = weather.loc[2091,['SeaLevel']]

In [686]:
#Check if missing values are still there
weather.loc[weather['SeaLevel'] == 'M']

Empty DataFrame
Columns: [Station, Date, Tmax, Tmin, Tavg, Depart, DewPoint, WetBulb, Heat, Cool, Sunrise, Sunset, CodeSum, Depth, SnowFall, PrecipTotal, StnPressure, SeaLevel, ResultSpeed, ResultDir, AvgSpeed]
Index: []

In [687]:
#Convert column to float
weather['SeaLevel'] = weather['SeaLevel'].apply(float)

**Impute for Tavg**
- Assume Stations 1 and 2 have the same Tavg on the same day

In [688]:
weather.loc[weather['Tavg'] == 'M']

Station       Date  Tmax  Tmin Tavg Depart  DewPoint  WetBulb Heat Cool  \
7           2 2007-05-04    78    51    M      M        42     50.0    M    M   
505         2 2008-07-08    86    46    M      M        68     71.0    M    M   
675         2 2008-10-01    62    46    M      M        41     47.0    M    M   
1637        2 2011-07-22   100    71    M      M        70     74.0    M    M   
2067        2 2012-08-22    84    72    M      M        51     61.0    M    M   
2211        2 2013-05-02    71    42    M      M        39     45.0    M    M   
2501        2 2013-09-24    91    52    M      M        48     54.0    M    M   
2511        2 2013-09-29    84    53    M      M        48     54.0    M    M   
2525        2 2013-10-06    76    48    M      M        44     50.0    M    M   
2579        2 2014-05-02    80    47    M      M        43     47.0    M    M   
2811        2 2014-08-26    86    49    M      M        68     71.0    M    M   

     Sunrise Sunset     CodeSum Depth SnowFall  PrecipTotal  StnPressure  \
7          -      -                 M        M         0.00        29.36   
505        -      -       TS RA     M        M         0.28        29.16   
675        -      -                 M        M         0.00        29.30   
1637       -      -  TS TSRA BR     M        M         0.14        29.23   
2067       -      -                 M        M         0.00        29.39   
2211       -      -                 M        M         0.00        29.51   
2501       -      -                 M        M         0.00        29.33   
2511       -      -       RA BR     M        M         0.22        29.36   
2525       -      -    RA DZ BR     M        M         0.06        29.10   
2579       -      -          RA     M        M         0.04        29.10   
2811       -      -                 M        M         0.01        29.41   

      SeaLevel  ResultSpeed  ResultDir  AvgSpeed  
7        30.04         10.1          7      10.4  
505      29.80          7.4         24       8.3  
675      29.96         10.9         33      11.0  
1637     29.86          3.8         10       8.2  
2067     30.07          4.7         19       5.8  
2211     30.17         15.8          2      16.1  
2501     30.00          5.8          9       7.7  
2511     30.01          6.3         36       7.8  
2525     29.76         10.1         25      10.6  
2579     29.79         10.7         23      11.9  
2811     30.04          1.3         15       5.8

In [689]:
#Define function to calculate Tavg by finding the average of Tmax and Tmin
def calc_tavg(row):
    if row['Tavg'] == 'M':
        row['Tavg'] = (row['Tmax'] + row['Tmin'])/2
    return row

weather = weather.apply(calc_tavg, axis = 1)

In [690]:
#Check some of the rows for function output
weather.loc[[7,505,675]]

Station       Date  Tmax  Tmin  Tavg Depart  DewPoint  WetBulb Heat Cool  \
7          2 2007-05-04    78    51  64.5      M        42     50.0    M    M   
505        2 2008-07-08    86    46  66.0      M        68     71.0    M    M   
675        2 2008-10-01    62    46  54.0      M        41     47.0    M    M   

    Sunrise Sunset CodeSum Depth SnowFall  PrecipTotal  StnPressure  SeaLevel  \
7         -      -             M        M         0.00        29.36     30.04   
505       -      -   TS RA     M        M         0.28        29.16     29.80   
675       -      -             M        M         0.00        29.30     29.96   

     ResultSpeed  ResultDir  AvgSpeed  
7           10.1          7      10.4  
505          7.4         24       8.3  
675         10.9         33      11.0

In [691]:
#Check if missing values are still there
weather.loc[weather['Tavg'] == 'M']

Empty DataFrame
Columns: [Station, Date, Tmax, Tmin, Tavg, Depart, DewPoint, WetBulb, Heat, Cool, Sunrise, Sunset, CodeSum, Depth, SnowFall, PrecipTotal, StnPressure, SeaLevel, ResultSpeed, ResultDir, AvgSpeed]
Index: []

In [692]:
#Convert column to float
weather['Tavg'] = weather['Tavg'].apply(float)

**Impute for Heat and Cool**
- Assume Stations 1 and 2 have the same Heat and Cool on the same day

In [693]:
weather[(weather['Heat'] == 'M')| (weather['Cool'] == 'M')]

Station       Date  Tmax  Tmin  Tavg Depart  DewPoint  WetBulb Heat  \
7           2 2007-05-04    78    51  64.5      M        42     50.0    M   
505         2 2008-07-08    86    46  66.0      M        68     71.0    M   
675         2 2008-10-01    62    46  54.0      M        41     47.0    M   
1637        2 2011-07-22   100    71  85.5      M        70     74.0    M   
2067        2 2012-08-22    84    72  78.0      M        51     61.0    M   
2211        2 2013-05-02    71    42  56.5      M        39     45.0    M   
2501        2 2013-09-24    91    52  71.5      M        48     54.0    M   
2511        2 2013-09-29    84    53  68.5      M        48     54.0    M   
2525        2 2013-10-06    76    48  62.0      M        44     50.0    M   
2579        2 2014-05-02    80    47  63.5      M        43     47.0    M   
2811        2 2014-08-26    86    49  67.5      M        68     71.0    M   

     Cool Sunrise Sunset     CodeSum Depth SnowFall  PrecipTotal  StnPressure  \
7       M       -      -                 M        M         0.00        29.36   
505     M       -      -       TS RA     M        M         0.28        29.16   
675     M       -      -                 M        M         0.00        29.30   
1637    M       -      -  TS TSRA BR     M        M         0.14        29.23   
2067    M       -      -                 M        M         0.00        29.39   
2211    M       -      -                 M        M         0.00        29.51   
2501    M       -      -                 M        M         0.00        29.33   
2511    M       -      -       RA BR     M        M         0.22        29.36   
2525    M       -      -    RA DZ BR     M        M         0.06        29.10   
2579    M       -      -          RA     M        M         0.04        29.10   
2811    M       -      -                 M        M         0.01        29.41   

      SeaLevel  ResultSpeed  ResultDir  AvgSpeed  
7        30.04         10.1          7      10.4  
505      29.80          7.4         24       8.3  
675      29.96         10.9         33      11.0  
1637     29.86          3.8         10       8.2  
2067     30.07          4.7         19       5.8  
2211     30.17         15.8          2      16.1  
2501     30.00          5.8          9       7.7  
2511     30.01          6.3         36       7.8  
2525     29.76         10.1         25      10.6  
2579     29.79         10.7         23      11.9  
2811     30.04          1.3         15       5.8

In [694]:
#Cool and Heat are based on how much cooler or hotter 65 is compared to Tavg
def calc_cool_heat(row):
    if row['Heat'] == 'M' or row['Cool'] == 'M':
        diff = 65 - row['Tavg']
        if diff > 0:
            row['Heat'] = diff
            row['Cool'] = 0
        elif diff < 0:
            row['Cool'] = diff * -1
            row['Heat'] = 0
        else:
            row['Heat'] = 0
            row['Cool'] = 0
    return row

weather = weather.apply(calc_cool_heat, axis = 1)

In [695]:
#Check some of the rows for function output
weather.loc[[7,505,675]]

Station       Date  Tmax  Tmin  Tavg Depart  DewPoint  WetBulb  Heat  \
7          2 2007-05-04    78    51  64.5      M        42     50.0   0.5   
505        2 2008-07-08    86    46  66.0      M        68     71.0     0   
675        2 2008-10-01    62    46  54.0      M        41     47.0  11.0   

    Cool Sunrise Sunset CodeSum Depth SnowFall  PrecipTotal  StnPressure  \
7      0       -      -             M        M         0.00        29.36   
505  1.0       -      -   TS RA     M        M         0.28        29.16   
675    0       -      -             M        M         0.00        29.30   

     SeaLevel  ResultSpeed  ResultDir  AvgSpeed  
7       30.04         10.1          7      10.4  
505     29.80          7.4         24       8.3  
675     29.96         10.9         33      11.0

In [696]:
#Check if missing values are still there
weather[(weather['Heat'] == 'M')| (weather['Cool'] == 'M')]

Empty DataFrame
Columns: [Station, Date, Tmax, Tmin, Tavg, Depart, DewPoint, WetBulb, Heat, Cool, Sunrise, Sunset, CodeSum, Depth, SnowFall, PrecipTotal, StnPressure, SeaLevel, ResultSpeed, ResultDir, AvgSpeed]
Index: []

In [697]:
#Convert column to float
weather['Heat'] = weather['Heat'].apply(float)
weather['Cool'] = weather['Cool'].apply(float)

**Impute for Depth and SnowFall**
- Assume Stations 1 and 2 have the same Depth and SnowFall on the same day

In [698]:
weather.loc[weather['SnowFall'] == 'M']

Station       Date  Tmax  Tmin  Tavg Depart  DewPoint  WetBulb  Heat  \
1           2 2007-05-01    84    52  68.0      M        51     57.0   0.0   
3           2 2007-05-02    60    43  52.0      M        42     47.0  13.0   
5           2 2007-05-03    67    48  58.0      M        40     50.0   7.0   
7           2 2007-05-04    78    51  64.5      M        42     50.0   0.5   
9           2 2007-05-05    66    54  60.0      M        39     50.0   5.0   
11          2 2007-05-06    68    52  60.0      M        30     46.0   5.0   
13          2 2007-05-07    84    50  67.0      M        39     53.0   0.0   
15          2 2007-05-08    80    60  70.0      M        57     63.0   0.0   
17          2 2007-05-09    76    63  70.0      M        60     63.0   0.0   
19          2 2007-05-10    83    59  71.0      M        52     61.0   0.0   
21          2 2007-05-11    73    49  61.0      M        44     51.0   4.0   
23          2 2007-05-12    65    47  56.0      M        37     46.0   9.0   
25          2 2007-05-13    69    44  57.0      M        32     46.0   8.0   
27          2 2007-05-14    90    54  72.0      M        45     58.0   0.0   
29          2 2007-05-15    82    56  69.0      M        56     61.0   0.0   
31          2 2007-05-16    64    45  55.0      M        42     47.0  10.0   
33          2 2007-05-17    61    44  53.0      M        32     43.0  12.0   
35          2 2007-05-18    70    43  57.0      M        31     47.0   8.0   
37          2 2007-05-19    80    56  68.0      M        37     53.0   0.0   
39          2 2007-05-20    69    44  57.0      M        41     45.0   8.0   
41          2 2007-05-21    79    46  63.0      M        50     57.0   2.0   
43          2 2007-05-22    87    60  74.0      M        44     58.0   0.0   
45          2 2007-05-23    89    66  78.0      M        48     61.0   0.0   
47          2 2007-05-24    88    66  77.0      M        53     63.0   0.0   
49          2 2007-05-25    66    57  62.0      M        46     53.0   3.0   
51          2 2007-05-26    70    50  60.0      M        55     57.0   5.0   
53          2 2007-05-27    75    59  67.0      M        49     57.0   0.0   
55          2 2007-05-28    76    54  65.0      M        49     57.0   0.0   
57          2 2007-05-29    88    65  77.0      M        59     66.0   0.0   
59          2 2007-05-30    89    70  80.0      M        57     66.0   0.0   
61          2 2007-05-31    80    68  74.0      M        61     66.0   0.0   
63          2 2007-06-01    86    67  77.0      M        63     67.0   0.0   
65          2 2007-06-02    81    68  75.0      M        62     67.0   0.0   
67          2 2007-06-03    77    64  71.0      M        60     64.0   0.0   
69          2 2007-06-04    72    56  64.0      M        57     60.0   1.0   
71          2 2007-06-05    63    51  57.0      M        47     52.0   8.0   
73          2 2007-06-06    73    48  61.0      M        47     55.0   4.0   
75          2 2007-06-07    92    71  82.0      M        61     68.0   0.0   
77          2 2007-06-08    81    63  72.0      M        54     62.0   0.0   
79          2 2007-06-09    79    57  68.0      M        49     58.0   0.0   
81          2 2007-06-10    81    61  71.0      M        50     60.0   0.0   
83          2 2007-06-11    85    65  75.0      M        51     61.0   0.0   
85          2 2007-06-12    82    66  74.0      M        51     61.0   0.0   
87          2 2007-06-13    86    68  77.0      M        53     62.0   0.0   
89          2 2007-06-14    89    68  79.0      M        54     63.0   0.0   
91          2 2007-06-15    89    67  78.0      M        56     65.0   0.0   
93          2 2007-06-16    92    68  80.0      M        61     68.0   0.0   
95          2 2007-06-17    91    71  81.0      M        65     70.0   0.0   
97          2 2007-06-18    89    73  81.0      M        65     70.0   0.0   
99          2 2007-06-19    81    65  73.0      M        55     63.0   0.0   
101         2 2007-06-20    

In [699]:
weather[(weather['SnowFall'] == 'M') & (weather['PrecipTotal'] == 'M')]

Empty DataFrame
Columns: [Station, Date, Tmax, Tmin, Tavg, Depart, DewPoint, WetBulb, Heat, Cool, Sunrise, Sunset, CodeSum, Depth, SnowFall, PrecipTotal, StnPressure, SeaLevel, ResultSpeed, ResultDir, AvgSpeed]
Index: []

**Observations:**
Since SnowFall is a type of precipitation, it should be taken into account in PrecipTotal. Also, there are no rows where both SnowFall and PrecipTotal are missing, so it should be safe to remove SnowFall. Additionally, since Depth is a measure of the amount of SnowFall, and in our case has as many missing values as Snowfall, Depth will be removed as well.

In [700]:
weather.drop(columns = ['SnowFall', 'Depth'], inplace = True)

**Impute for Depart**
- Assume that the Depart values of Stations 1 and 2 are calculated from the same Normal temperature

In [701]:
weather.loc[weather['Depart'] == 'M']

Station       Date  Tmax  Tmin  Tavg Depart  DewPoint  WetBulb  Heat  \
1           2 2007-05-01    84    52  68.0      M        51     57.0   0.0   
3           2 2007-05-02    60    43  52.0      M        42     47.0  13.0   
5           2 2007-05-03    67    48  58.0      M        40     50.0   7.0   
7           2 2007-05-04    78    51  64.5      M        42     50.0   0.5   
9           2 2007-05-05    66    54  60.0      M        39     50.0   5.0   
11          2 2007-05-06    68    52  60.0      M        30     46.0   5.0   
13          2 2007-05-07    84    50  67.0      M        39     53.0   0.0   
15          2 2007-05-08    80    60  70.0      M        57     63.0   0.0   
17          2 2007-05-09    76    63  70.0      M        60     63.0   0.0   
19          2 2007-05-10    83    59  71.0      M        52     61.0   0.0   
21          2 2007-05-11    73    49  61.0      M        44     51.0   4.0   
23          2 2007-05-12    65    47  56.0      M        37     46.0   9.0   
25          2 2007-05-13    69    44  57.0      M        32     46.0   8.0   
27          2 2007-05-14    90    54  72.0      M        45     58.0   0.0   
29          2 2007-05-15    82    56  69.0      M        56     61.0   0.0   
31          2 2007-05-16    64    45  55.0      M        42     47.0  10.0   
33          2 2007-05-17    61    44  53.0      M        32     43.0  12.0   
35          2 2007-05-18    70    43  57.0      M        31     47.0   8.0   
37          2 2007-05-19    80    56  68.0      M        37     53.0   0.0   
39          2 2007-05-20    69    44  57.0      M        41     45.0   8.0   
41          2 2007-05-21    79    46  63.0      M        50     57.0   2.0   
43          2 2007-05-22    87    60  74.0      M        44     58.0   0.0   
45          2 2007-05-23    89    66  78.0      M        48     61.0   0.0   
47          2 2007-05-24    88    66  77.0      M        53     63.0   0.0   
49          2 2007-05-25    66    57  62.0      M        46     53.0   3.0   
51          2 2007-05-26    70    50  60.0      M        55     57.0   5.0   
53          2 2007-05-27    75    59  67.0      M        49     57.0   0.0   
55          2 2007-05-28    76    54  65.0      M        49     57.0   0.0   
57          2 2007-05-29    88    65  77.0      M        59     66.0   0.0   
59          2 2007-05-30    89    70  80.0      M        57     66.0   0.0   
61          2 2007-05-31    80    68  74.0      M        61     66.0   0.0   
63          2 2007-06-01    86    67  77.0      M        63     67.0   0.0   
65          2 2007-06-02    81    68  75.0      M        62     67.0   0.0   
67          2 2007-06-03    77    64  71.0      M        60     64.0   0.0   
69          2 2007-06-04    72    56  64.0      M        57     60.0   1.0   
71          2 2007-06-05    63    51  57.0      M        47     52.0   8.0   
73          2 2007-06-06    73    48  61.0      M        47     55.0   4.0   
75          2 2007-06-07    92    71  82.0      M        61     68.0   0.0   
77          2 2007-06-08    81    63  72.0      M        54     62.0   0.0   
79          2 2007-06-09    79    57  68.0      M        49     58.0   0.0   
81          2 2007-06-10    81    61  71.0      M        50     60.0   0.0   
83          2 2007-06-11    85    65  75.0      M        51     61.0   0.0   
85          2 2007-06-12    82    66  74.0      M        51     61.0   0.0   
87          2 2007-06-13    86    68  77.0      M        53     62.0   0.0   
89          2 2007-06-14    89    68  79.0      M        54     63.0   0.0   
91          2 2007-06-15    89    67  78.0      M        56     65.0   0.0   
93          2 2007-06-16    92    68  80.0      M        61     68.0   0.0   
95          2 2007-06-17    91    71  81.0      M        65     70.0   0.0   
97          2 2007-06-18    89    73  81.0      M        65     70.0   0.0   
99          2 2007-06-19    81    65  73.0      M        55     63.0   0.0   
101         2 2007-06-20    

At a glance, seems like all the rows with missing Depart data are from Station 2

In [702]:
weather.loc[weather['Depart'] == 'M','Station'].unique()

array([2], dtype=int64)

Confirmed that all rows with missing Depart data are from Station 2

In [703]:
weather[(weather['Depart'] != 'M') & (weather['Station'] == 2)]

Empty DataFrame
Columns: [Station, Date, Tmax, Tmin, Tavg, Depart, DewPoint, WetBulb, Heat, Cool, Sunrise, Sunset, CodeSum, PrecipTotal, StnPressure, SeaLevel, ResultSpeed, ResultDir, AvgSpeed]
Index: []

None of the Station 2 datapoints have any Depart data

In [704]:
weather[(weather['Depart'] == 'M') & (weather['Station'] == 1)]

Empty DataFrame
Columns: [Station, Date, Tmax, Tmin, Tavg, Depart, DewPoint, WetBulb, Heat, Cool, Sunrise, Sunset, CodeSum, PrecipTotal, StnPressure, SeaLevel, ResultSpeed, ResultDir, AvgSpeed]
Index: []

None of the Station 1 datapoints are missing any Depart data

In [705]:
weather.loc[weather['Station'] ==1]

Station       Date  Tmax  Tmin  Tavg Depart  DewPoint  WetBulb  Heat  \
0           1 2007-05-01    83    50  67.0     14        51     56.0   0.0   
2           1 2007-05-02    59    42  51.0     -3        42     47.0  14.0   
4           1 2007-05-03    66    46  56.0      2        40     48.0   9.0   
6           1 2007-05-04    66    49  58.0      4        41     50.0   7.0   
8           1 2007-05-05    66    53  60.0      5        38     49.0   5.0   
10          1 2007-05-06    68    49  59.0      4        30     46.0   6.0   
12          1 2007-05-07    83    47  65.0     10        41     54.0   0.0   
14          1 2007-05-08    82    54  68.0     12        58     62.0   0.0   
16          1 2007-05-09    77    61  69.0     13        59     63.0   0.0   
18          1 2007-05-10    84    56  70.0     14        52     60.0   0.0   
20          1 2007-05-11    70    51  61.0      4        42     51.0   4.0   
22          1 2007-05-12    64    46  55.0     -2        36     46.0  10.0   
24          1 2007-05-13    69    43  56.0     -2        33     46.0   9.0   
26          1 2007-05-14    90    56  73.0     15        47     59.0   0.0   
28          1 2007-05-15    80    57  69.0     11        56     61.0   0.0   
30          1 2007-05-16    66    44  55.0     -4        43     48.0  10.0   
32          1 2007-05-17    62    43  53.0     -6        32     43.0  12.0   
34          1 2007-05-18    71    42  57.0     -3        30     46.0   8.0   
36          1 2007-05-19    80    56  68.0      8        39     53.0   0.0   
38          1 2007-05-20    69    43  56.0     -5        40     44.0   9.0   
40          1 2007-05-21    80    44  62.0      1        50     56.0   3.0   
42          1 2007-05-22    87    55  71.0     10        46     58.0   0.0   
44          1 2007-05-23    89    60  75.0     14        49     61.0   0.0   
46          1 2007-05-24    88    63  76.0     14        54     63.0   0.0   
48          1 2007-05-25    70    56  63.0      1        44     53.0   2.0   
50          1 2007-05-26    65    49  57.0     -5        55     56.0   8.0   
52          1 2007-05-27    75    57  66.0      4        47     56.0   0.0   
54          1 2007-05-28    79    50  65.0      2        47     56.0   0.0   
56          1 2007-05-29    88    60  74.0     10        58     65.0   0.0   
58          1 2007-05-30    87    66  77.0     13        58     65.0   0.0   
60          1 2007-05-31    78    65  72.0      8        61     65.0   0.0   
62          1 2007-06-01    85    62  74.0     10        63     66.0   0.0   
64          1 2007-06-02    81    65  73.0      9        63     67.0   0.0   
66          1 2007-06-03    78    62  70.0      6        60     63.0   0.0   
68          1 2007-06-04    71    58  65.0      1        58     60.0   0.0   
70          1 2007-06-05    64    47  56.0     -9        48     51.0   9.0   
72          1 2007-06-06    71    44  58.0     -8        48     55.0   7.0   
74          1 2007-06-07    91    71  81.0     15        62     69.0   0.0   
76          1 2007-06-08    81    57  69.0      3        53     61.0   0.0   
78          1 2007-06-09    79    52  66.0      0        47     57.0   0.0   
80          1 2007-06-10    81    55  68.0      1        51     59.0   0.0   
82          1 2007-06-11    86    58  72.0      5        52     61.0   0.0   
84          1 2007-06-12    83    62  73.0      5        50     60.0   0.0   
86          1 2007-06-13    87    60  74.0      6        53     62.0   0.0   
88          1 2007-06-14    89    64  77.0      9        55     64.0   0.0   
90          1 2007-06-15    91    63  77.0      9        56     64.0   0.0   
92          1 2007-06-16    93    66  80.0     11        60     67.0   0.0   
94          1 2007-06-17    91    70  81.0     12        64     70.0   0.0   
96          1 2007-06-18    89    69  79.0      9        65     70.0   0.0   
98          1 2007-06-19    80    65  73.0      3        55     63.0   0.0   
100         1 2007-06-20    

In [706]:
weather.loc[weather['Depart'] == 'M',['Depart']] = 0

In [707]:
weather['Depart'] = weather['Depart'].apply(float)

In [708]:
weather.head()

Station       Date  Tmax  Tmin  Tavg  Depart  DewPoint  WetBulb  Heat  \
0        1 2007-05-01    83    50  67.0    14.0        51     56.0   0.0   
1        2 2007-05-01    84    52  68.0     0.0        51     57.0   0.0   
2        1 2007-05-02    59    42  51.0    -3.0        42     47.0  14.0   
3        2 2007-05-02    60    43  52.0     0.0        42     47.0  13.0   
4        1 2007-05-03    66    46  56.0     2.0        40     48.0   9.0   

   Cool Sunrise Sunset CodeSum  PrecipTotal  StnPressure  SeaLevel  \
0   2.0    0448   1849                  0.0        29.10     29.82   
1   3.0       -      -                  0.0        29.18     29.82   
2   0.0    0447   1850      BR          0.0        29.38     30.09   
3   0.0       -      -   BR HZ          0.0        29.44     30.08   
4   0.0    0446   1851                  0.0        29.39     30.12   

   ResultSpeed  ResultDir  AvgSpeed  
0          1.7         27       9.2  
1          2.7         25       9.6  
2         13.0          4      13.4  
3         13.3          2      13.4  
4         11.7          7      11.9

In [709]:
a = weather.loc[1,['Tavg']] - weather.loc[0,['Tavg']]
a = float(a)
b = weather.loc[0,['Depart']] + a
b

Depart    15.0
Name: 0, dtype: object

In [710]:
#Depart is the difference between Tavg and normal temperature. 
#Assuming both stations have the same normal temperature, use Station 1 values to calculate depart of Station 2
for i in range(1,weather.shape[0],2):
    tavg_diff = weather.loc[i,['Tavg']] - weather.loc[i-1,['Tavg']]
    tavg_diff = float(tavg_diff)
    weather.loc[i,['Depart']] = weather.loc[i-1,['Depart']] + tavg_diff

In [711]:
# Check function output
weather.head()

Station       Date  Tmax  Tmin  Tavg  Depart  DewPoint  WetBulb  Heat  \
0        1 2007-05-01    83    50  67.0    14.0        51     56.0   0.0   
1        2 2007-05-01    84    52  68.0    15.0        51     57.0   0.0   
2        1 2007-05-02    59    42  51.0    -3.0        42     47.0  14.0   
3        2 2007-05-02    60    43  52.0    -2.0        42     47.0  13.0   
4        1 2007-05-03    66    46  56.0     2.0        40     48.0   9.0   

   Cool Sunrise Sunset CodeSum  PrecipTotal  StnPressure  SeaLevel  \
0   2.0    0448   1849                  0.0        29.10     29.82   
1   3.0       -      -                  0.0        29.18     29.82   
2   0.0    0447   1850      BR          0.0        29.38     30.09   
3   0.0       -      -   BR HZ          0.0        29.44     30.08   
4   0.0    0446   1851                  0.0        29.39     30.12   

   ResultSpeed  ResultDir  AvgSpeed  
0          1.7         27       9.2  
1          2.7         25       9.6  
2         13.0          4      13.4  
3         13.3          2      13.4  
4         11.7          7      11.9

----
### Impute Dash (-) Values

In [712]:
dash = weather.isin(['-']).sum()

dash_df = []
for key, value in dash.sort_values(ascending=False).items():
    if value != 0:
        dash_row = []
        dash_row.append(key)
        dash_row.append(value)
        percentage = round(value/weather.shape[0]*100,2)
        dash_row.append(percentage)
        dash_df.append(dash_row)
dash_df = pd.DataFrame(dash_df, columns = ['Feature', 'No. of dash values', 'Percentage of dash values'] )
dash_df

Feature  No. of dash values  Percentage of dash values
0  Sunrise                1472                       50.0
1   Sunset                1472                       50.0

**Impute for Sunrise and Sunset**
- Assume Stations 1 and 2 have the same Sunrise and Sunset on the same day

In [713]:
weather[(weather['Sunrise'] == '-') | (weather['Sunset'] == '-')]

Station       Date  Tmax  Tmin  Tavg  Depart  DewPoint  WetBulb  Heat  \
1           2 2007-05-01    84    52  68.0    15.0        51     57.0   0.0   
3           2 2007-05-02    60    43  52.0    -2.0        42     47.0  13.0   
5           2 2007-05-03    67    48  58.0     4.0        40     50.0   7.0   
7           2 2007-05-04    78    51  64.5    10.5        42     50.0   0.5   
9           2 2007-05-05    66    54  60.0     5.0        39     50.0   5.0   
11          2 2007-05-06    68    52  60.0     5.0        30     46.0   5.0   
13          2 2007-05-07    84    50  67.0    12.0        39     53.0   0.0   
15          2 2007-05-08    80    60  70.0    14.0        57     63.0   0.0   
17          2 2007-05-09    76    63  70.0    14.0        60     63.0   0.0   
19          2 2007-05-10    83    59  71.0    15.0        52     61.0   0.0   
21          2 2007-05-11    73    49  61.0     4.0        44     51.0   4.0   
23          2 2007-05-12    65    47  56.0    -1.0        37     46.0   9.0   
25          2 2007-05-13    69    44  57.0    -1.0        32     46.0   8.0   
27          2 2007-05-14    90    54  72.0    14.0        45     58.0   0.0   
29          2 2007-05-15    82    56  69.0    11.0        56     61.0   0.0   
31          2 2007-05-16    64    45  55.0    -4.0        42     47.0  10.0   
33          2 2007-05-17    61    44  53.0    -6.0        32     43.0  12.0   
35          2 2007-05-18    70    43  57.0    -3.0        31     47.0   8.0   
37          2 2007-05-19    80    56  68.0     8.0        37     53.0   0.0   
39          2 2007-05-20    69    44  57.0    -4.0        41     45.0   8.0   
41          2 2007-05-21    79    46  63.0     2.0        50     57.0   2.0   
43          2 2007-05-22    87    60  74.0    13.0        44     58.0   0.0   
45          2 2007-05-23    89    66  78.0    17.0        48     61.0   0.0   
47          2 2007-05-24    88    66  77.0    15.0        53     63.0   0.0   
49          2 2007-05-25    66    57  62.0     0.0        46     53.0   3.0   
51          2 2007-05-26    70    50  60.0    -2.0        55     57.0   5.0   
53          2 2007-05-27    75    59  67.0     5.0        49     57.0   0.0   
55          2 2007-05-28    76    54  65.0     2.0        49     57.0   0.0   
57          2 2007-05-29    88    65  77.0    13.0        59     66.0   0.0   
59          2 2007-05-30    89    70  80.0    16.0        57     66.0   0.0   
61          2 2007-05-31    80    68  74.0    10.0        61     66.0   0.0   
63          2 2007-06-01    86    67  77.0    13.0        63     67.0   0.0   
65          2 2007-06-02    81    68  75.0    11.0        62     67.0   0.0   
67          2 2007-06-03    77    64  71.0     7.0        60     64.0   0.0   
69          2 2007-06-04    72    56  64.0     0.0        57     60.0   1.0   
71          2 2007-06-05    63    51  57.0    -8.0        47     52.0   8.0   
73          2 2007-06-06    73    48  61.0    -5.0        47     55.0   4.0   
75          2 2007-06-07    92    71  82.0    16.0        61     68.0   0.0   
77          2 2007-06-08    81    63  72.0     6.0        54     62.0   0.0   
79          2 2007-06-09    79    57  68.0     2.0        49     58.0   0.0   
81          2 2007-06-10    81    61  71.0     4.0        50     60.0   0.0   
83          2 2007-06-11    85    65  75.0     8.0        51     61.0   0.0   
85          2 2007-06-12    82    66  74.0     6.0        51     61.0   0.0   
87          2 2007-06-13    86    68  77.0     9.0        53     62.0   0.0   
89          2 2007-06-14    89    68  79.0    11.0        54     63.0   0.0   
91          2 2007-06-15    89    67  78.0    10.0        56     65.0   0.0   
93          2 2007-06-16    92    68  80.0    11.0        61     68.0   0.0   
95          2 2007-06-17    91    71  81.0    12.0        65     70.0   0.0   
97          2 2007-06-18    89    73  81.0    11.0        65     70.0   0.0   
99          2 2007-06-19    81    65  73.0     3.0      

Seems like only Station 2 datapoints have '-' in Sunrise/Sunset values

In [714]:
weather[(weather['Sunrise'] == '-') | (weather['Sunset'] == '-')]['Station'].unique()

array([2], dtype=int64)

Confirmed that only Station 2 datapoints have '-' values

In [715]:
for i in range(1,weather.shape[0],2):
    weather.loc[i,['Sunrise']] = weather.loc[i-1,['Sunrise']]
    weather.loc[i,['Sunset']] = weather.loc[i-1,['Sunset']]

In [716]:
#Check some of the rows to see the imputed values
weather.head()

Station       Date  Tmax  Tmin  Tavg  Depart  DewPoint  WetBulb  Heat  \
0        1 2007-05-01    83    50  67.0    14.0        51     56.0   0.0   
1        2 2007-05-01    84    52  68.0    15.0        51     57.0   0.0   
2        1 2007-05-02    59    42  51.0    -3.0        42     47.0  14.0   
3        2 2007-05-02    60    43  52.0    -2.0        42     47.0  13.0   
4        1 2007-05-03    66    46  56.0     2.0        40     48.0   9.0   

   Cool Sunrise Sunset CodeSum  PrecipTotal  StnPressure  SeaLevel  \
0   2.0    0448   1849                  0.0        29.10     29.82   
1   3.0    0448   1849                  0.0        29.18     29.82   
2   0.0    0447   1850      BR          0.0        29.38     30.09   
3   0.0    0447   1850   BR HZ          0.0        29.44     30.08   
4   0.0    0446   1851                  0.0        29.39     30.12   

   ResultSpeed  ResultDir  AvgSpeed  
0          1.7         27       9.2  
1          2.7         25       9.6  
2         13.0          4      13.4  
3         13.3          2      13.4  
4         11.7          7      11.9

In [717]:
#Check for anymore dash values
weather.isin(['-']).sum()

Station        0
Date           0
Tmax           0
Tmin           0
Tavg           0
Depart         0
DewPoint       0
WetBulb        0
Heat           0
Cool           0
Sunrise        0
Sunset         0
CodeSum        0
PrecipTotal    0
StnPressure    0
SeaLevel       0
ResultSpeed    0
ResultDir      0
AvgSpeed       0
dtype: int64

----
### Adding Features
For easier manipulation and EDA, add Year, Month, Week and Day of Week to dataset

In [718]:
weather['Year'] = weather['Date'].apply(lambda x: x.year)
weather['Month'] = weather['Date'].apply(lambda x: x.month)
weather['Week'] = weather['Date'].apply(lambda x: x.week)
weather['DayOfWeek'] = weather['Date'].apply(lambda x: x.dayofweek)

In [719]:
#Export for use in EDA notebook
weather.to_csv('../assets/weather_cleaned.csv', index=False)

----
## Train Dataset

In [720]:
train.head()

Date                                            Address  \
0  2007-05-29  4100 North Oak Park Avenue, Chicago, IL 60634,...   
1  2007-05-29  4100 North Oak Park Avenue, Chicago, IL 60634,...   
2  2007-05-29  6200 North Mandell Avenue, Chicago, IL 60646, USA   
3  2007-05-29    7900 West Foster Avenue, Chicago, IL 60656, USA   
4  2007-05-29    7900 West Foster Avenue, Chicago, IL 60656, USA   

                  Species  Block           Street  Trap  \
0  CULEX PIPIENS/RESTUANS     41   N OAK PARK AVE  T002   
1          CULEX RESTUANS     41   N OAK PARK AVE  T002   
2          CULEX RESTUANS     62    N MANDELL AVE  T007   
3  CULEX PIPIENS/RESTUANS     79     W FOSTER AVE  T015   
4          CULEX RESTUANS     79     W FOSTER AVE  T015   

              AddressNumberAndStreet   Latitude  Longitude  AddressAccuracy  \
0  4100  N OAK PARK AVE, Chicago, IL  41.954690 -87.800991                9   
1  4100  N OAK PARK AVE, Chicago, IL  41.954690 -87.800991                9   
2   6200  N MANDELL AVE, Chicago, IL  41.994991 -87.769279                9   
3    7900  W FOSTER AVE, Chicago, IL  41.974089 -87.824812                8   
4    7900  W FOSTER AVE, Chicago, IL  41.974089 -87.824812                8   

   NumMosquitos  WnvPresent  
0             1           0  
1             1           0  
2             1           0  
3             1           0  
4             4           0

In [721]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10506 entries, 0 to 10505
Data columns (total 12 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   Date                    10506 non-null  object 
 1   Address                 10506 non-null  object 
 2   Species                 10506 non-null  object 
 3   Block                   10506 non-null  int64  
 4   Street                  10506 non-null  object 
 5   Trap                    10506 non-null  object 
 6   AddressNumberAndStreet  10506 non-null  object 
 7   Latitude                10506 non-null  float64
 8   Longitude               10506 non-null  float64
 9   AddressAccuracy         10506 non-null  int64  
 10  NumMosquitos            10506 non-null  int64  
 11  WnvPresent              10506 non-null  int64  
dtypes: float64(2), int64(4), object(6)
memory usage: 985.1+ KB


In [722]:
train['Date'] = pd.to_datetime(train['Date'])

In [723]:
#Add the same additional features as weather
train['Year'] = train['Date'].apply(lambda x: x.year)
train['Month'] = train['Date'].apply(lambda x: x.month)
train['Week'] = train['Date'].apply(lambda x: x.week)
train['DayOfWeek'] = train['Date'].apply(lambda x: x.dayofweek)

In [724]:
#Export for use in a later notebook
train.to_csv('../assets/train_cleaned.csv', index=False)

----
## Test Dataset

In [725]:
test.head()

Id        Date                                            Address  \
0   1  2008-06-11  4100 North Oak Park Avenue, Chicago, IL 60634,...   
1   2  2008-06-11  4100 North Oak Park Avenue, Chicago, IL 60634,...   
2   3  2008-06-11  4100 North Oak Park Avenue, Chicago, IL 60634,...   
3   4  2008-06-11  4100 North Oak Park Avenue, Chicago, IL 60634,...   
4   5  2008-06-11  4100 North Oak Park Avenue, Chicago, IL 60634,...   

                  Species  Block           Street  Trap  \
0  CULEX PIPIENS/RESTUANS     41   N OAK PARK AVE  T002   
1          CULEX RESTUANS     41   N OAK PARK AVE  T002   
2           CULEX PIPIENS     41   N OAK PARK AVE  T002   
3        CULEX SALINARIUS     41   N OAK PARK AVE  T002   
4         CULEX TERRITANS     41   N OAK PARK AVE  T002   

              AddressNumberAndStreet  Latitude  Longitude  AddressAccuracy  
0  4100  N OAK PARK AVE, Chicago, IL  41.95469 -87.800991                9  
1  4100  N OAK PARK AVE, Chicago, IL  41.95469 -87.800991                9  
2  4100  N OAK PARK AVE, Chicago, IL  41.95469 -87.800991                9  
3  4100  N OAK PARK AVE, Chicago, IL  41.95469 -87.800991                9  
4  4100  N OAK PARK AVE, Chicago, IL  41.95469 -87.800991                9

In [726]:
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 116293 entries, 0 to 116292
Data columns (total 11 columns):
 #   Column                  Non-Null Count   Dtype  
---  ------                  --------------   -----  
 0   Id                      116293 non-null  int64  
 1   Date                    116293 non-null  object 
 2   Address                 116293 non-null  object 
 3   Species                 116293 non-null  object 
 4   Block                   116293 non-null  int64  
 5   Street                  116293 non-null  object 
 6   Trap                    116293 non-null  object 
 7   AddressNumberAndStreet  116293 non-null  object 
 8   Latitude                116293 non-null  float64
 9   Longitude               116293 non-null  float64
 10  AddressAccuracy         116293 non-null  int64  
dtypes: float64(2), int64(3), object(6)
memory usage: 9.8+ MB


In [727]:
test['Date'] = pd.to_datetime(test['Date'])

In [728]:
#Add the same additional features as train
test['Year'] = test['Date'].apply(lambda x: x.year)
test['Month'] = test['Date'].apply(lambda x: x.month)
test['Week'] = test['Date'].apply(lambda x: x.week)
test['DayOfWeek'] = test['Date'].apply(lambda x: x.dayofweek)

In [729]:
#Export for use in a later notebook
test.to_csv('../assets/test_cleaned.csv', index=False)

----
## Spray Dataset

In [730]:
spray.head()

Date        Time   Latitude  Longitude
0  2011-08-29  6:56:58 PM  42.391623 -88.089163
1  2011-08-29  6:57:08 PM  42.391348 -88.089163
2  2011-08-29  6:57:18 PM  42.391022 -88.089157
3  2011-08-29  6:57:28 PM  42.390637 -88.089158
4  2011-08-29  6:57:38 PM  42.390410 -88.088858

In [731]:
spray.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14835 entries, 0 to 14834
Data columns (total 4 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   Date       14835 non-null  object 
 1   Time       14251 non-null  object 
 2   Latitude   14835 non-null  float64
 3   Longitude  14835 non-null  float64
dtypes: float64(2), object(2)
memory usage: 463.7+ KB


In [732]:
spray['Date'] = pd.to_datetime(spray['Date'])

In [733]:
spray.isnull().sum()

Date           0
Time         584
Latitude       0
Longitude      0
dtype: int64

In [734]:
spray['Time'].isnull().sum()/spray.shape[0]

0.039366363329962926

**Observations:**
- Only around 4% of Time data is missing

In [735]:
spray.loc[spray['Time'].isnull()]

Date Time   Latitude  Longitude
1030 2011-09-07  NaN  41.987092 -87.794286
1031 2011-09-07  NaN  41.987620 -87.794382
1032 2011-09-07  NaN  41.988004 -87.794574
1033 2011-09-07  NaN  41.988292 -87.795486
1034 2011-09-07  NaN  41.988100 -87.796014
1035 2011-09-07  NaN  41.986372 -87.794862
1036 2011-09-07  NaN  41.986228 -87.795582
1037 2011-09-07  NaN  41.984836 -87.793998
1038 2011-09-07  NaN  41.984836 -87.794670
1039 2011-09-07  NaN  41.984884 -87.795198
1040 2011-09-07  NaN  41.982820 -87.793182
1041 2011-09-07  NaN  41.982772 -87.793950
1042 2011-09-07  NaN  41.982772 -87.795006
1043 2011-09-07  NaN  41.983444 -87.795246
1044 2011-09-07  NaN  41.984068 -87.795438
1045 2011-09-07  NaN  41.984596 -87.795534
1046 2011-09-07  NaN  41.984980 -87.795630
1047 2011-09-07  NaN  41.986708 -87.796110
1048 2011-09-07  NaN  41.987524 -87.796302
1049 2011-09-07  NaN  41.988820 -87.796638
1050 2011-09-07  NaN  41.989444 -87.796830
1051 2011-09-07  NaN  41.990068 -87.796974
1052 2011-09-07  NaN  41.988244 -87.797022
1053 2011-09-07  NaN  41.988196 -87.797742
1054 2011-09-07  NaN  41.988196 -87.798366
1055 2011-09-07  NaN  41.988196 -87.798942
1056 2011-09-07  NaN  41.988196 -87.799422
1057 2011-09-07  NaN  41.986372 -87.796494
1058 2011-09-07  NaN  41.986372 -87.797310
1059 2011-09-07  NaN  41.986372 -87.798030
1060 2011-09-07  NaN  41.986420 -87.798558
1061 2011-09-07  NaN  41.986612 -87.799278
1062 2011-09-07  NaN  41.986708 -87.799758
1063 2011-09-07  NaN  41.986900 -87.800238
1064 2011-09-07  NaN  41.984980 -87.796302
1065 2011-09-07  NaN  41.985028 -87.797166
1066 2011-09-07  NaN  41.985028 -87.797694
1067 2011-09-07  NaN  41.985076 -87.798270
1068 2011-09-07  NaN  41.985076 -87.798942
1069 2011-09-07  NaN  41.985124 -87.799662
1070 2011-09-07  NaN  41.985652 -87.797550
1071 2011-09-07  NaN  41.984452 -87.797598
1072 2011-09-07  NaN  41.983828 -87.797598
1073 2011-09-07  NaN  41.983396 -87.797646
1074 2011-09-07  NaN  41.982772 -87.797550
1075 2011-09-07  NaN  41.982772 -87.796734
1076 2011-09-07  NaN  41.982820 -87.796014
1077 2011-09-07  NaN  41.982820 -87.795390
1078 2011-09-07  NaN  41.983540 -87.798270
1079 2011-09-07  NaN  41.983732 -87.799230
1080 2011-09-07  NaN  41.983876 -87.799902
1081 2011-09-07  NaN  41.983972 -87.800574
1082 2011-09-07  NaN  41.984068 -87.801103
1083 2011-09-07  NaN  41.984356 -87.801727
1084 2011-09-07  NaN  41.984596 -87.802255
1085 2011-09-07  NaN  41.984788 -87.802591
1086 2011-09-07  NaN  41.984932 -87.802927
1087 2011-09-07  NaN  41.985220 -87.803551
1088 2011-09-07  NaN  41.985364 -87.800334
1089 2011-09-07  NaN  41.985556 -87.800863
1090 2011-09-07  NaN  41.985748 -87.801199
1091 2011-09-07  NaN  41.985844 -87.801583
1092 2011-09-07  NaN  41.985988 -87.798942
1093 2011-09-07  NaN  41.985556 -87.799374
1094 2011-09-07  NaN  41.984404 -87.800478
1095 2011-09-07  NaN  41.983732 -87.801247
1096 2011-09-07  NaN  41.983588 -87.801919
1097 2011-09-07  NaN  41.983876 -87.802735
1098 2011-09-07  NaN  41.984116 -87.803263
1099 2011-09-07  NaN  41.984308 -87.803551
1100 2011-09-07  NaN  41.984548 -87.803983
1101 2011-09-07  NaN  41.984740 -87.804367
1102 2011-09-07  NaN  41.984932 -87.804943
1103 2011-09-07  NaN  41.985268 -87.805711
1104 2011-09-07  NaN  41.985508 -87.806143
1105 2011-09-07  NaN  41.985652 -87.806479
1106 2011-09-07  NaN  41.985796 -87.806767
1107 2011-09-07  NaN  41.985652 -87.804079
1108 2011-09-07  NaN  41.985988 -87.804655
1109 2011-09-07  NaN  41.986324 -87.805039
1110 2011-09-07  NaN  41.986564 -87.805375
1111 2011-09-07  NaN  41.987140 -87.805519
1112 2011-09-07  NaN  41.987860 -87.805615
1113 2011-09-07  NaN  41.988292 -87.805615
1114 2011-09-07  NaN  41.988820 -87.805087
1115 2011-09-07  NaN  41.989204 -87.804655
1116 2011-09-07  NaN  41.989588 -87.804175
1117 2011-09-07  NaN  41.989972 -87.803791
1118 2011-09-07  NaN  41.990164 -87.803407
1119 2011-09-07  NaN  41.990452 -87.802975
1120 2011-09-07  NaN  41.990644 -87.802495
1121 2011-09-07  NaN  41.990644 -87.801775
1122 2011-09

In [736]:
spray.loc[spray['Time'].isnull()].groupby('Date').count()

Time  Latitude  Longitude
Date                                 
2011-09-07     0       584        584

**Observations:**
- All the missing Time data are from the same day, 2011-09-07

In [737]:
spray['Date'].unique()

array(['2011-08-29T00:00:00.000000000', '2011-09-07T00:00:00.000000000',
       '2013-07-17T00:00:00.000000000', '2013-07-25T00:00:00.000000000',
       '2013-08-08T00:00:00.000000000', '2013-08-15T00:00:00.000000000',
       '2013-08-16T00:00:00.000000000', '2013-08-22T00:00:00.000000000',
       '2013-08-29T00:00:00.000000000', '2013-09-05T00:00:00.000000000'],
      dtype='datetime64[ns]')

In [738]:
spray['Date'].nunique()

10

In [739]:
spray.groupby('Date').count()

Time  Latitude  Longitude
Date                                 
2011-08-29    95        95         95
2011-09-07  1530      2114       2114
2013-07-17  2202      2202       2202
2013-07-25  1607      1607       1607
2013-08-08  1195      1195       1195
2013-08-15  2668      2668       2668
2013-08-16   141       141        141
2013-08-22  1587      1587       1587
2013-08-29  2302      2302       2302
2013-09-05   924       924        924

**Observations:**
- We only have spray data from 10 different days

**Impute values for Time**
- It would not make sense to impute 1 specific time value for 584 instances of spraying
- Since only 4% of the data is missing, to drop the missing data

In [740]:
spray.dropna(inplace=True)
spray.shape

(14251, 4)

In [741]:
#Check that missing values are gone
spray.isnull().sum()

Date         0
Time         0
Latitude     0
Longitude    0
dtype: int64

In [742]:
#Add extra features for easier manipulation in later notebooks
spray['Hour'] = pd.to_datetime(spray['Time'], format='%I:%M:%S %p').dt.hour
spray['Minute'] = pd.to_datetime(spray['Time'], format='%I:%M:%S %p').dt.minute
spray['Second'] = pd.to_datetime(spray['Time'], format='%I:%M:%S %p').dt.second

In [743]:
spray.head()

Date        Time   Latitude  Longitude  Hour  Minute  Second
0 2011-08-29  6:56:58 PM  42.391623 -88.089163    18      56      58
1 2011-08-29  6:57:08 PM  42.391348 -88.089163    18      57       8
2 2011-08-29  6:57:18 PM  42.391022 -88.089157    18      57      18
3 2011-08-29  6:57:28 PM  42.390637 -88.089158    18      57      28
4 2011-08-29  6:57:38 PM  42.390410 -88.088858    18      57      38

In [744]:
#Export for use in a later notebook
spray.to_csv('../assets/spray_cleaned.csv', index=False)